## AUV-to-transponder Range Estimation Application using UnetStack
It is a common practice to attach a transponder to various underwater assets (both static and mobile) for short and long term field deployments. These transponders can act as a beacon that can be utilized for localization. An underwater vehicle (e.g. AUV, ROV) will be able to do sequential ranging to find the location of the transponder during a search and rescue operation.

Normally, specialized transmitters are required to send a signal to these transponders to trigger a response. However, due to the software defined nature of Subnero modems, it is fairly easy to develop and application that will query a transponder and find the range to it.


In this post, we showcase a fully functional transponder ranging application used to ping an Applied Acoustics 219A transponder and do ranging with the recorded signal. This work has been presented in `TODO`.
The Applied Acoustics 219A transponder is set to receive a 22 kHz tonal. This will trigger a response at 30.5 kHz after 30 ms. We use the modem to send the 22 kHz signal and does a 500 ms long baseband signal recording using `RecordBasebandSignalReq` to make sure the modem begins records long enough to have the response from the pinger from within `TODO` range. The captured signal is then Hilbert transformed to do envelop detection. We use a threshold detection to find the start of the received signal. The modems provide tx start time. Using this informaiton, the range is determined accurately.

This application is developed using Jupyter Notebook, in Python usign the UnetPy framework.

In [3]:
import numpy as np
import arlpy.signal as asig
from arlpy.plot import *
from unetpy import *

### Connect to the modem

In [ ]:
modem = UnetGateway('192.168.1.34')

In [ ]:
phy = modem.agent('phy')
modem.subscribe(phy)

### Set passband block count & signal power level
In order to get the transponder to respond to our signal, we can use an arbitrary waveform transmission and reception. We need to set the passband block size for the recordings at the modem's physical layer for this using `phy.pbsblk` parameter. We also might want to set the signal power level depending on the environment.

In [ ]:
fs = 96000
sigLen = 5e-3
# phy.pbsblk = 45056
# phy.signalPowerLevel = -10

In [ ]:
def flush_modem():
    while modem.receive(timeout=1000):
        pass

### Generater the signal to be transmitted

In [ ]:
tx = asig.cw(22000, sigLen, fs*2).tolist()

### Start baseband signal reception and transmit the signal

In [4]:
flush_modem()
phy.npulses = 1
#phy.pulsedelay = 100
phy.pbscnt = 1
phy << org_arl_unet_bb.TxBasebandSignalReq(signal=tx, fc=0)
rx = modem.receive(org_arl_unet_bb.RxBasebandSignalNtf, 5000)
txntf = modem.receive(timeout=5000)
txTime = txntf.txTime
rxTime = rx.rxTime

NameError: name 'flush_modem' is not defined

### Plot the recorded signal & PSD

In [ ]:
plot(rx.signal, fs=rx.fs, maxpts=48000, hold=True)
txStart=(txTime-rxTime)/1e6
vlines(txStart, color='orange')

In [ ]:
psd(rx.signal, fs=fs, nfft=512, noverlap=None, window='hanning', color=None, style='solid', thickness=1, marker=None, filled=False, size=6, title=None, xlabel='Frequency (Hz)', ylabel='Power spectral density (dB/Hz)', xlim=None, ylim=None, width=None, height=None, hold=False, interactive=None)

In [ ]:
rx.signal.tofile("rxSignal.txt",sep=",",format="%s")

In [42]:
# Delete later
fs=96000
tx = []
x = []
siglen = 20e-3
file = open('rxsignal.txt', 'r') 
string = file.readline()
# print(string)
for x in string.split(','):
    tx.append(float(x))

txStart=81000/1e6

In [24]:
shift = (txStart+siglen)
# rx1 = rx.signal[int(shift):]
rx1 = tx[int(shift*fs):]
env = asig.envelope(rx1)
threshold = 0.9
edge = np.flatnonzero((env[:-1] < threshold) & (env[1:] > threshold))+1

In [32]:
psd(tx, fs=fs, hold=True)
psd(rx1, fs=fs)

In [36]:
plot(tx, maxpts = 96000)

In [37]:
plot(rx1, maxpts = 96000)

In [31]:
plot(env, maxpts = 96000, hold=True)
vlines(edge[0], color='orange')

In [38]:
plot(tx, fs=fs, maxpts = 96000, hold=True)
#txStart=(txTime-rxTime)/1e6
rxStart=(shift+edge[0]/fs)
vlines(txStart, hold=True, color='orange')
vlines(rxStart, color='purple')

In [43]:
print ('Tx Start = ', txStart, 's')
print ('Rx Start = ', rxStart, 's')
travelTime = rxStart-txStart-30e-3
print ('Round trip time = ', travelTime, 's')
soundSpeed = 1536
print ('Range = ', soundSpeed * travelTime, 'm')

Tx Start =  0.081 s
Rx Start =  0.11221875 s
Round trip time =  0.0012187500000000046 s
Range =  1.872000000000007 m


In [ ]:
modem.shutdown()